In [1]:
%%javascript
IPython.OutputArea.prototype._should_scroll = function(lines) {
    return false;
}

<IPython.core.display.Javascript object>

In [2]:
import pyLPM
import pandas as pd
import RBFN
import RBF
import numpy as np

In [3]:
walter = pd.read_csv('data/walker.csv')

In [4]:
walter.drop(columns=['Id','U','T'], inplace=True)

In [5]:
walter.head()

X     Y      V
0  11.0   8.0    0.0
1   8.0  30.0    0.0
2   9.0  48.0  224.4
3   8.0  69.0  434.4
4   9.0  90.0  412.1

In [6]:
walter['Z'] = np.zeros(len(walter))

In [7]:
walter.head()

X     Y      V    Z
0  11.0   8.0    0.0  0.0
1   8.0  30.0    0.0  0.0
2   9.0  48.0  224.4  0.0
3   8.0  69.0  434.4  0.0
4   9.0  90.0  412.1  0.0

In [8]:
exhaust = pd.read_csv('data/walker_fivebyfive_exhaust.csv')

In [9]:
exhaust = exhaust.sort_values(by=['YG+ Gravity Center+','XG+ Gravity Center+'])

In [10]:
exhaust.head()

SN+ Sample Number (READONLY)+  XG+ Gravity Center+  YG+ Gravity Center+  \
0                                1                  8.0                  8.0   
58                              59                 13.0                  8.0   
116                            117                 18.0                  8.0   
174                            175                 23.0                  8.0   
232                            233                 28.0                  8.0   

     copy_stat_mean    iqd     ok  ok_pt  
0              7.65   3.41  38.67  38.69  
58             9.37   1.76  28.49  28.45  
116           13.77  20.53  44.10  44.19  
174           51.79  36.18  36.43  36.53  
232           72.53  38.44  33.22  33.15

In [11]:
coordinates = walter[['X','Y','Z']]

# Settinng parameters

In [12]:
n_clus = 200

In [13]:
centers = RBFN.cluster_centers(n_clus=n_clus,
                               coordinates=coordinates)

In [14]:
rbf_n = RBFN.RBFN(cluster_centers=centers, 
                  sigma=None,
                  function='gaussian')

In [15]:
rbf_n.sigma

array([18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209341,
       18.5209341, 18.5209341, 18.5209341, 18.5209341, 18.5209

# Training

In [16]:
rbf_n.weights = np.random.randn(n_clus+1)

In [17]:
X_train, X_test, y_train, y_test = RBFN.train_test_sets_builder(walter, 'X', 'Y', 'Z', 'V', test_size=0.33)

In [18]:
rbf_n.train(3000, X_train, y_train, learning_rate_w=-0.00006, learning_rate_sigma=None)

Epoch: 0 
 loss: 43144130.25342588
Epoch: 500 
 loss: 7537070.127768674
Epoch: 1000 
 loss: 6596289.268507332
Epoch: 1500 
 loss: 6096042.616692304
Epoch: 2000 
 loss: 5792397.800029022
Epoch: 2500 
 loss: 5588111.147227529


# Testing

In [19]:
test_predictions = rbf_n.predict(X_test)

In [20]:
pyLPM.plots.scatter2d(x=test_predictions, y=y_test)

# Predicting on grid and comparing with the truth

In [21]:
grid = pyLPM.utils.autogrid(x=walter.X, y=walter.Y, z=walter.Z, sx=5, sy=5, sz=1)

In [22]:
X = pyLPM.utils.add_coord(grid)

In [23]:
predict_train = rbf_n.predict(X)

In [24]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_train,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [25]:
pyLPM.plots.scatter2d(x=predict_train, y=exhaust.copy_stat_mean)

In [26]:
rbf_n.train(2000, X_train, y_train, learning_rate_w=None, learning_rate_sigma=0.00006)

Epoch: 0 
 loss: 5438686.6222227095
Epoch: 500 
 loss: 449600030.8490665
Epoch: 1000 
 loss: 257420970.30274612
Epoch: 1500 
 loss: 225016429.06246576


# testing

In [27]:
test_predictions = rbf_n.predict(X_test)

In [28]:
pyLPM.plots.scatter2d(x=test_predictions, y=y_test)

# Predicting on a grid

In [29]:
grid = pyLPM.utils.autogrid(x=walter.X, y=walter.Y, z=walter.Z, sx=5, sy=5, sz=1)

In [30]:
X = pyLPM.utils.add_coord(grid)

In [31]:
predict_train = rbf_n.predict(X)

In [32]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_train,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [33]:
pyLPM.plots.scatter2d(x=predict_train, y=exhaust.copy_stat_mean)

In [34]:
max(rbf_n.sigma)

2780.976085683294

In [35]:
min(rbf_n.sigma)

-2564.551560324329